In [1]:
import xarray as xr
from pathlib import Path
import time

In [2]:
vars = ['pr', 'tas', 'tasmax', 'tasmin', 'hurs']

In [3]:
locs = {
    
    # # Student request
    # 'suffolk': {'lon': 1.057185, 'lat': 52.285113, 'reason': 'student'},
    # 'pontypridd': {'lon': -3.342, 'lat': 51.602, 'reason': 'student'},
    # 'usk': {'lon': -2.75 , 'lat': 51.75, 'reason': 'student'},
    # 'denbigh': {'lon': -3.5 , 'lat': 53.25, 'reason': 'student'},
    # 'larkana': {'lon': 68.20 , 'lat': 27.56, 'reason': 'student'},
    # 'rome': {'lon': 12.4822 , 'lat': 41.8967, 'reason': 'student'},
    # 'tunis': {'lon': 10.1815 , 'lat': 36.8065, 'reason': 'student'},
    # 'fakenham': {'lon': 0.8493 , 'lat': 52.8313, 'reason': 'student'},
    'tokyo': {'lon': 139.5, 'lat': 35.7, 'reason': 'student'},

    # # Heat Wave Hotspots
    # 'islamabad': {'lon': 73.0479, 'lat': 33.6844, 'reason': 'heat waves'},
    # 'phoenix': {'lon': -112.0740, 'lat': 33.4484, 'reason': 'heat waves'},
    # 'delhi': {'lon': 77.1025, 'lat': 28.7041, 'reason': 'heat waves'},
    # 'baghdad': {'lon': 44.3661, 'lat': 33.3152, 'reason': 'heat waves'},
    # 'athens': {'lon': 23.7275, 'lat': 37.9838, 'reason': 'heat waves'},
    # 'shanghai': {'lon': 121.4737, 'lat': 31.2304, 'reason': 'heat waves and humidity extremes'},

    # # High Precipitation Extremes
    # 'mumbai': {'lon': 72.8777, 'lat': 19.0760, 'reason': 'monsoonal precipitation extremes'},
    # 'jakarta': {'lon': 106.8456, 'lat': -6.2088, 'reason': 'coastal flooding and precipitation extremes'},
    # 'new_orleans': {'lon': -90.0715, 'lat': 29.9511, 'reason': 'hurricane precipitation and sea level rise'},
    # 'dhaka': {'lon': 90.4125, 'lat': 23.8103, 'reason': 'monsoonal precipitation and flood risks'},

    # 'lhr': {'lon': -0.4551, 'lat': 51.4680, 'reason': 'has obs data'},  # London Heathrow
}

In [4]:
# prepare point lists once
names = list(locs.keys())
lats  = [locs[n]["lat"] for n in names]
lons  = [locs[n]["lon"] for n in names]

# Xarray paired selection arrays
lat_da = xr.DataArray(lats, dims="name", coords={"name": names})
lon_da = xr.DataArray(lons, dims="name", coords={"name": names})

for var in vars:
    print(var)
    start_var = time.time()
    with xr.open_mfdataset(f'W5E5/{var}_W5E5v2.0_*.nc', chunks={'time': -1}) as ds:


        start_read = time.time()
        out = ds[var].sel(
                    lat=lat_da,
                    lon=lon_da,
                    method="nearest"
                ).load()
        end_read = time.time()
        print(f'   Time for reading NetCDF: {(end_read - start_read)/60:.2f} m')
        
        for name in names:
            
            print('   ' + name)
            odir = f"../timeseries/{name}/netcdf/{var}/"
            Path(odir).mkdir(parents=True, exist_ok=True)
            tas = out.sel(name=name)
            tas.to_netcdf(f'{odir}/W5E5v2.0_{var}_{name}_daily.nc')

            idir = f"../timeseries/{name}/netcdf/{var}/"
            odir = f"../timeseries/{name}/csv/{var}/"
            Path(odir).mkdir(parents=True, exist_ok=True)
            da = xr.open_dataarray(f'{idir}/W5E5v2.0_{var}_{name}_daily.nc')
            da.to_dataframe().to_csv(f'{odir}/W5E5v2.0_{var}_{name}_daily.csv')

    end_var = time.time()
    print(f'Time for variable {var}: {(end_var - start_var)/60:.2f} m')

pr
   Time for reading NetCDF: 1.67 m
   tokyo
Time for variable pr: 1.75 m
tas
   Time for reading NetCDF: 1.14 m
   tokyo
Time for variable tas: 1.15 m
tasmax
   Time for reading NetCDF: 1.03 m
   tokyo
Time for variable tasmax: 1.04 m
tasmin
   Time for reading NetCDF: 1.07 m
   tokyo
Time for variable tasmin: 1.08 m
hurs
   Time for reading NetCDF: 1.09 m
   tokyo
Time for variable hurs: 1.09 m


In [5]:
'Done'

'Done'